- Date : 2020.9.23
- Author : Jiwon Jang

- folium을 활용하여 OSM기반 지도 표출
- 어떤 건물을 표출해야하는지 고민

__[표출 정보]__  
__(space)__  
- tile로 작업
- 도로망,상점 정보,연구지역 (단계 구분도)
- 이태원역 : 37.5342356,126.9934594

- layer 1 : OSM
- layer 2 : Building point
- layer 3 : Road shapefile(geojson)
- layer 4 : Instagram Buzz / heatmap - choropleth
- layer 5 : grid
- layer 6 : Simulation result / Timestamp geojson / heatmap - choropleth


__(Time)__
- timestamp
- 전체 지역의 추세 표출

__[reference]__
- Interactive Choropleth Map of Washington DC using Folium and Python : https://medium.com/@lindsayrallen1/interactive-choropleth-map-of-washington-dc-using-folium-and-python-2794708514d5
- grid : https://www.jpytr.com/post/analysinggeographicdatawithfolium/
- folium plugin : https://dailyheumsi.tistory.com/85
- geojson(shapefile) : https://ducj.tistory.com/39

In [26]:
from folium import plugins
from folium.plugins import MarkerCluster
from folium.plugins import HeatMap
from folium.plugins import MousePosition 
from tqdm import tqdm
import pickle, folium, datetime, json
import pandas as pd

In [2]:
# # # load - address coordinates data - 한글 -> 영어로 변경
with open('AddressCoordinates.pickle', 'rb') as f:
    Addresses = pickle.load(f)

In [3]:
# save - address coordinates
# with open('INSTASTAMP.pickle', 'wb') as f:
#     pickle.dump(INSTASTAMP, f, pickle.HIGHEST_PROTOCOL)

# # # load
with open('INSTASTAMP.pickle', 'rb') as f:
    INSTASTAMP = pickle.load(f)

In [4]:
dateList = list(set(INSTASTAMP['Date']))

In [5]:
dateList.sort()

In [6]:
# save - address coordinates
# with open('TimeLists.pickle', 'wb') as f:
#     pickle.dump(TimeLists, f, pickle.HIGHEST_PROTOCOL)

# # # load
# with open('TimeLists.pickle', 'rb') as f:
#     TimeLists = pickle.load(f)

In [7]:
# save - address coordinates
# with open('HeatTimes.pickle', 'wb') as f:
#     pickle.dump(HeatTimes, f, pickle.HIGHEST_PROTOCOL)

# # # load
with open('HeatTimes.pickle', 'rb') as f:
    HeatTimes = pickle.load(f)

In [8]:
geojson1 = json.load(open("/Users/jiwonjang/python_tutorial/ve_env/githubBlog/data/ITW_gridGeojson.json", 
                          encoding='utf-8'))
geojson2 = json.load(open("/Users/jiwonjang/python_tutorial/ve_env/githubBlog/data/ITW_researchAreaGeojson.json", 
                          encoding='utf-8'))

# Make Maps!

In [205]:
center = [37.5342356,126.9934594] # center point - Itaewon station
m = folium.Map(location=center,control_scale=True, zoom_start=15)
fg = folium.FeatureGroup(name='All Information')

In [206]:
m.add_child(fg)

In [207]:
# cluster map - layer 1 : building layer
mcg = folium.plugins.MarkerCluster(control=False)
m.add_child(mcg)
g1 = folium.plugins.FeatureGroupSubGroup(mcg, 'BUILDING(341)')
# g1 = folium.plugins.FeatureGroupSubGroup(fg, 'BUILDING')
m.add_child(g1)

In [208]:
### all buildings
# for i in Addresses[:10]:
#     addr = i['address']
#     y = float(i['coor_y'])
#     x = float(i['coor_x'])
#     site = [y, x]
    
#     folium.Marker(
#       location=site,
#       popup= addr,
#       icon=folium.Icon(color='red',icon='star')
#     ).add_to(g1)

In [209]:
## specific building
for i in HeatTimes[-1]:
    pop = 'Instagram Buzz : ' + str(i[2])
    y = i[0] # latitude
    x = i[1] # longtitude
    site = [y, x]
    
    folium.Marker(
      location=site,
      popup= pop,
      icon=folium.Icon(color='red',icon='star')
    ).add_to(g1)

In [210]:
g2 = folium.plugins.FeatureGroupSubGroup(fg, 'HeatMap(Instagram Buzz)')
m.add_child(g2)

In [211]:
# layer 2
HeatMap(HeatTimes[-1]).add_to(g2)
# folium.LayerControl(collapsed=False).add_to(m) # tile layer 추가

In [212]:
# layer 3
g3 = folium.plugins.FeatureGroupSubGroup(fg, 'Simulation Environment(Grid)')
m.add_child(g3)

# folium.Choropleth(
#     geo_data=geojson1,
#     name='choropleth',
#     data = 0,
#     key_on='feature.id',
#     fill_color='BuGn',
#     fill_opacity=0.3,
#     line_opacity=0.35).add_to(g3)

# folium.GeoJson(geojson1, smooth_factor=0.5).add_to(g3) # default

folium.GeoJson(geojson1, smooth_factor=0.5,
              style_function = lambda x : {
        'color' : "#1f1a95",
        'weight' : 1,
        'opacity': 0.15,
        'fillColor' : 'black',
        }).add_to(g3)

In [213]:
# layer 4
g4 = folium.plugins.FeatureGroupSubGroup(fg, 'Research Area')
m.add_child(g4)

# folium.Choropleth(
#     geo_data=geojson2,
#     name='choropleth',
#     data = 0,
#     key_on='feature.id',
#     fill_color='PuBuGn',
#     fill_opacity=0.3,
#     line_opacity=0.35).add_to(g4)

# folium.GeoJson(geojson2, smooth_factor=0.5).add_to(g4) # default

folium.GeoJson(geojson2, smooth_factor=0.5,
              style_function = lambda x : {
        'color' : "#59008e",
        'weight' : 1,
        'opacity': 1,
        'fillColor' : 'grey',
        }).add_to(g4)


In [214]:
folium.LayerControl(collapsed=False).add_to(m) # tile layer 추가

In [215]:
formatter = "function(num) {return L.Util.formatNum(num, 3) + ' º ';};" 
MousePosition(position='topright', separator=' | ', empty_string='NaN', 
              lng_first=True, num_digits=20, prefix='Coordinates:', 
              lat_formatter=formatter, lng_formatter=formatter ).add_to(m)

In [216]:
# # ScrollZoomToggler
# plugins.ScrollZoomToggler().add_to(m)

# minimap
minimap = plugins.MiniMap() 
m.add_child(minimap)

plugins.Fullscreen(position='topright', title='Expand me', 
                   title_cancel='Exit me', force_separate_button=True).add_to(m) 

In [217]:
m

In [218]:
# m.save('ITW_baseMap_20201011.html')